In [1]:
import numpy as np
from sklearn.gaussian_process.kernels import Matern, RBF
from sklearn.tree import DecisionTreeRegressor

import plotly
import plotly.express as px

from docs.mse_estimator import ErrorComparer
from docs.data_generation import gen_rbf_X, gen_matern_X, gen_cov_mat
from docs.plotting_utils import gen_model_barplots
from spe.estimators import new_y_est, cp_arbitrary, by_spatial

In [2]:
np.random.seed(1)

# Generalized BY Comparison
Here we compare ```spe.estimators.cp_arbitrary``` to a generalized version of the BY estimator, ```spe.estimators.by_spatial```, to estimate MSE on simulated data.

In [3]:
## number of realizations to run
niter = 100

## data generation parameters
gsize=10
n=10**2
p=200
s=200
delta = 0.75
snr = 2.
tr_frac = .25

noise_kernel = 'matern'
noise_length_scale = 1.
noise_nu = .5

X_kernel = 'matern'
X_length_scale = 5.
X_nu = 2.5

## ErrorComparer parameters
alpha = .05
nboot = 100
k = 5

models = [DecisionTreeRegressor(max_depth=5, max_features='sqrt')]

ests = [
    new_y_est,
    new_y_est,
    cp_arbitrary,
    by_spatial,
    by_spatial,
    by_spatial,
]
est_kwargs = [
    {'alpha': None,
    'full_refit': False},
    {'alpha': .05,
    'full_refit': False},
    {'alpha': alpha, 
    'use_trace_corr': False, 
    'nboot': nboot},
    {'alpha': .05, 
    'nboot': nboot},
    {'alpha': 1., 
    'nboot': nboot},
    {'alpha': 5., 
    'nboot': nboot},
]

## plot parameters
est_names = ["GenCp .05", "BY .05", "BY 1.", "BY 5."]
model_names = ["Decision Tree"]

In [4]:
err_cmp = ErrorComparer()

In [5]:
nx = ny = int(np.sqrt(n))
xs = np.linspace(0, gsize, nx)
ys = np.linspace(0, gsize, ny)
c_x, c_y = np.meshgrid(xs, ys)
c_x = c_x.flatten()
c_y = c_y.flatten()
coord = np.stack([c_x, c_y]).T

In [6]:
if noise_kernel == 'rbf':
    Sigma_t = gen_cov_mat(c_x, c_y, RBF(length_scale=noise_length_scale))
elif noise_kernel == 'matern':
    Sigma_t = gen_cov_mat(c_x, c_y, Matern(length_scale=noise_length_scale, nu=noise_nu))
else:
    Sigma_t = np.eye(n)
    
Cov_y_ystar = delta*Sigma_t
Sigma_t = delta*Sigma_t + (1-delta)*np.eye(n)

if noise_kernel == 'rbf' or noise_kernel == 'matern':
    Chol_y = np.linalg.cholesky(Sigma_t)
else:
    Chol_y = np.eye(n)

In [7]:
if X_kernel == 'rbf':
    Sigma_X = gen_cov_mat(c_x, c_y, RBF(length_scale=X_length_scale))
elif X_kernel == 'matern':
    Sigma_X = gen_cov_mat(c_x, c_y, Matern(length_scale=X_length_scale, nu=X_nu))
else:
    Sigma_X = np.eye(n)

if X_kernel == 'rbf' or X_kernel == 'matern':
    Chol_X = np.linalg.cholesky(Sigma_X)
else:
    Chol_X = np.eye(n)

X = Chol_X @ np.random.randn(n,p)

if X_kernel == 'rbf':
    X_spikes = gen_rbf_X(c_x, c_y, p)
elif X_kernel == 'matern':
    X_spikes = gen_matern_X(c_x, c_y, p, length_scale=X_length_scale, nu=X_nu)
else:
    X_spikes = np.random.randn(n,p)

X_iso = np.random.randn(n,p)

In [8]:
nx = ny = int(np.sqrt(n))
xs = np.linspace(0, 30, nx)
ys = np.linspace(0, 30, ny)
c_x, c_y = np.meshgrid(xs, ys)
c_x = c_x.flatten()
c_y = c_y.flatten()
coord = np.stack([c_x, c_y]).T

if X_kernel == 'rbf':
    Sigma_X_less = gen_cov_mat(c_x, c_y, RBF(length_scale=X_length_scale))
elif X_kernel == 'matern':
    Sigma_X_less = gen_cov_mat(c_x, c_y, Matern(length_scale=X_length_scale, nu=X_nu))
else:
    Sigma_X_less = np.eye(n)

if X_kernel == 'rbf' or X_kernel == 'matern':
    Chol_X_less = np.linalg.cholesky(Sigma_X_less)
else:
    Chol_X_less = np.eye(n)

X_less = Chol_X_less @ np.random.randn(n,p)

In [9]:
beta = np.zeros(p)
idx = np.random.choice(p,size=s,replace=False)
beta[idx] = np.random.uniform(-1,1,size=s)

In [10]:
tr_idx = np.ones(n, dtype=bool)

## Simulate $\begin{pmatrix} Y \\ Y^* \end{pmatrix} \sim \mathcal{N}\left(\begin{pmatrix} \mu \\ \mu \end{pmatrix}, \begin{pmatrix}\Sigma_Y & \Sigma_{Y, Y^*} \\ \Sigma_{Y^*, Y} & \Sigma_{Y}  \end{pmatrix}\right)$

### $X_{\cdot,i}$ independently generated by uniform spikes at locations, then interpolate based on cov matrix

In [11]:
spike_model_errs = []

for model in models:
    errs = err_cmp.compare(
        model,
        ests,
        est_kwargs,
        niter=niter,
        n=n,
        p=p,
        s=s,
        snr=snr, 
        X=X_spikes,
        beta=beta,
        coord=coord,
        Chol_y=Chol_y,
        Chol_ystar=None,
        Cov_y_ystar=Cov_y_ystar,
        tr_idx=tr_idx,
        fair=False,
        est_sigma=False,
    )
    spike_model_errs.append(errs)

  0%|          | 0/100 [00:00<?, ?it/s]

100%|██████████| 100/100 [00:47<00:00,  2.12it/s]


### $X_{i,\cdot} \sim \mathcal{N}(0, I\sigma^2)$

In [12]:
iid_model_errs = []

for model in models:
    errs = err_cmp.compare(
        model,
        ests,
        est_kwargs,
        niter=niter,
        n=n,
        p=p,
        s=s,
        snr=snr, 
        X=X_iso,
        beta=beta,
        coord=coord,
        Chol_y=Chol_y,
        Chol_ystar=None,
        Cov_y_ystar=Cov_y_ystar,
        tr_idx=tr_idx,
        fair=False,
        est_sigma=False,
    )
    iid_model_errs.append(errs)

100%|██████████| 100/100 [00:46<00:00,  2.15it/s]


In [13]:
plotly.offline.init_notebook_mode()
fig = gen_model_barplots(
    spike_model_errs + iid_model_errs,
    ["Corr X", "IID X"],
    est_names,
    title="BY Comparisons: Depth 5 Decision Tree, SSN",
    has_elev_err=True,
    err_bars=True,
    color_discrete_sequence=[px.colors.qualitative.Bold[i] for i in [0,6,7,8]],
    fig_name="by_comp",
)
fig.show()